In [1]:
import warnings
warnings.filterwarnings("ignore", category=UserWarning)

import requests, datetime
import pandas as pd
import numpy as np
from textblob import TextBlob
from transformers import pipeline
from bs4 import BeautifulSoup as bs

import matplotlib.pyplot as plt
%matplotlib inline

# Enable Google interactive table
from google.colab import data_table
data_table.enable_dataframe_formatter()

agent_info = {'User-Agent': 'Mozilla/5.0 (Windows NT 6.1; WOW64; rv:20.0) Gecko/20100101 Firefox/20.0'}

# Convert the sentiment label
# from: {-1:Negative, 0:Neutral, 1:Positive}
#   to: { 0:Negative, 2:Neutral, 1:Positive}
def convertSentimentLabel(label):
  if label == 0: return -1
  elif label == 2: return 0
  else: return label


# combine multiple words into one single word
# e.g. very good -> very_good
def combineWord(words):
  combined = ""
  for word in words:
    combined += word + "_"

  return combined[:len(combined)-1]


def convertTextBlobSentimentPolarity(polarity, positiveThreshod=0.1, negativeThreshod=-0.1):
  if polarity < negativeThreshod: return -1
  elif polarity > positiveThreshod: return 1
  else: return 0


# get the sentiment polarity and assessment from Textblob
def getTextBlobSentiments(content):
  tb = TextBlob(content)
  assessmentsList = []

  for assessments in tb.sentiment_assessments.assessments:
    assessmentsList.append((combineWord(assessments[0]), assessments[1]))

  return convertTextBlobSentimentPolarity(tb.polarity), tb.polarity, assessmentsList


def getLmScore(lm):
    x = lm[0]

    if x['label'] =="neutral":
        return 0
    elif x['label']  =="positive":
        return 1
    elif x['label']  =="negative":
        return -1

In [ ]:
# Use a tradition rule-based sentiment engine textblob
sentence = 'This demo is interesting'

print(sentence)
tb = TextBlob(sentence)
print('polarity=', tb.polarity)
tb.sentiment_assessments

This demo is interesting
polarity= 0.5


Sentiment(polarity=0.5, subjectivity=0.5, assessments=[(['interesting'], 0.5, 0.5, None)])

In [ ]:
lm_model = 'mrm8488/distilroberta-finetuned-financial-news-sentiment-analysis' # @param ["mrm8488/distilroberta-finetuned-financial-news-sentiment-analysis"] {allow-input: true}

lm_sentiment = pipeline("text-classification", model=lm_model)

config.json:   0%|          | 0.00/933 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/328M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/333 [00:00<?, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

Device set to use cpu


In [ ]:
print(getLmScore(lm_sentiment("The profit is great")))
print(getLmScore(lm_sentiment("The profit is the same")))
print(getLmScore(lm_sentiment("The profit is bad")))

1
0
-1


In [ ]:
splits = {'train': 'sent_train.csv', 'validation': 'sent_valid.csv'}
df = pd.read_csv("hf://datasets/zeroshot/twitter-financial-news-sentiment/" + splits["train"])

# Convert the sentiment label to {-1:Negative, 0:Neutral, 1:Positive}
df['polarity'] = df['label'].apply(convertSentimentLabel)
df[['text', 'polarity']]

text  polarity
0     $BYND - JPMorgan reels in expectations on Beyo...        -1
1     $CCL $RCL - Nomura points to bookings weakness...        -1
2     $CX - Cemex cut at Credit Suisse, J.P. Morgan ...        -1
3     $ESS: BTIG Research cuts to Neutral https://t....        -1
4     $FNKO - Funko slides after Piper Jaffray PT cu...        -1
...                                                 ...       ...
9538  The Week's Gainers and Losers on the Stoxx Eur...         0
9539  Tupperware Brands among consumer gainers; Unil...         0
9540  vTv Therapeutics leads healthcare gainers; Myo...         0
9541    WORK, XPO, PYX and AMKR among after hour movers         0
9542             YNDX, I, QD and OESX among tech movers         0

[9543 rows x 2 columns]

In [ ]:
df['textblob_polarity'], df['textblob_sentiment'], df['textblob_assessments'] = zip(*df['text'].apply(getTextBlobSentiments))
df[['text', 'polarity', 'textblob_polarity', 'textblob_assessments']]

text  polarity  \
0     $BYND - JPMorgan reels in expectations on Beyo...        -1   
1     $CCL $RCL - Nomura points to bookings weakness...        -1   
2     $CX - Cemex cut at Credit Suisse, J.P. Morgan ...        -1   
3     $ESS: BTIG Research cuts to Neutral https://t....        -1   
4     $FNKO - Funko slides after Piper Jaffray PT cu...        -1   
...                                                 ...       ...   
9538  The Week's Gainers and Losers on the Stoxx Eur...         0   
9539  Tupperware Brands among consumer gainers; Unil...         0   
9540  vTv Therapeutics leads healthcare gainers; Myo...         0   
9541    WORK, XPO, PYX and AMKR among after hour movers         0   
9542             YNDX, I, QD and OESX among tech movers         0   

      textblob_polarity textblob_assessments  
0                     0                   []  
1                     0                   []  
2                    -1     [(weak, -0.375)]  
3                     0                   []  
4                     0                   []  
...                 ...                  ...  
9538                 -1     [(losers, -0.2)]  
9539                 -1     [(losers, -0.2)]  
9540                 -1     [(losers, -0.2)]  
9541                  0                   []  
9542                  0                   []  

[9543 rows x 4 columns]

In [ ]:
#df['lm_polarity'] = df['text'].apply(lambda x: getLmScore(lm_sentiment(x)))
#df[['text', 'polarity', 'lm_polarity', 'textblob_polarity', 'textblob_sentiment', 'textblob_assessments']]

# To save time, use the saved results
df = pd.read_csv('https://raw.githubusercontent.com/kenwkliu/ideas/refs/heads/master/colab/data/NewsSentimentSmallLanguageModel.csv')

df['lm'] = (df['polarity'] == df['lm_polarity']).astype(int)
df['textblob'] = (df['polarity'] == df['textblob_polarity']).astype(int)
df[['text', 'polarity', 'lm_polarity', 'textblob_polarity', 'textblob_assessments']]

text  polarity  \
0     $BYND - JPMorgan reels in expectations on Beyo...        -1   
1     $CCL $RCL - Nomura points to bookings weakness...        -1   
2     $CX - Cemex cut at Credit Suisse, J.P. Morgan ...        -1   
3     $ESS: BTIG Research cuts to Neutral https://t....        -1   
4     $FNKO - Funko slides after Piper Jaffray PT cu...        -1   
...                                                 ...       ...   
9538  The Week's Gainers and Losers on the Stoxx Eur...         0   
9539  Tupperware Brands among consumer gainers; Unil...         0   
9540  vTv Therapeutics leads healthcare gainers; Myo...         0   
9541    WORK, XPO, PYX and AMKR among after hour movers         0   
9542             YNDX, I, QD and OESX among tech movers         0   

      lm_polarity  textblob_polarity textblob_assessments  
0               1                  0                   []  
1              -1                  0                   []  
2              -1                 -1   [('weak', -0.375)]  
3              -1                  0                   []  
4              -1                  0                   []  
...           ...                ...                  ...  
9538            0                 -1   [('losers', -0.2)]  
9539            1                 -1   [('losers', -0.2)]  
9540            1                 -1   [('losers', -0.2)]  
9541            0                  0                   []  
9542            0                  0                   []  

[9543 rows x 5 columns]

In [ ]:
print("Small LLM: {}".format(df['lm'].sum() / len(df['lm'])))
print("Textblob : {}".format(df['textblob'].sum() / len(df['lm'])))

Small LLM: 0.7402284396940165
Textblob : 0.5210101645184952


In [ ]:
#@title NVDA
ticker = 'NVDA'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=NVDA


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0    NVDA  2025-11-25  08:56AM   
1    NVDA  2025-11-25  08:48AM   
2    NVDA  2025-11-25  08:46AM   
3    NVDA  2025-11-25  08:45AM   
4    NVDA  2025-11-25  08:44AM   
..    ...         ...      ...   
95   NVDA  2025-11-24  12:09PM   
96   NVDA  2025-11-24  12:06PM   
97   NVDA  2025-11-24  12:03PM   
98   NVDA  2025-11-24  12:00PM   
99   NVDA  2025-11-24  12:00PM   

                                             Headline  
0   Google In Talks To Offer Its AI Chips To Meta;...  
1   Stock Market Today: Dow Jones Rises At Key Lev...  
2   Soft Retail Sales, Weak ADP Jobs Data May Shap...  
3   Google Just Hit the AI Accelerator--Is Nvidia'...  
4   Meta Platforms Weighs Multi-Billion-Dollar Dea...  
..                                                ...  
95  Alibaba Stock Jumps On Monday -- Here's What Y...  
96  Neobank Revolut Boosts Valuation to $75 Billio...  
97  Nvidia Stock Rises. The Tech Rally, China News...  
98  Elfun Trusts Significantly Reduces Stake in Br...  
99  1 Beaten-Down Artificial Intelligence (AI) Sto...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0    NVDA  2025-11-25  08:56AM   
1    NVDA  2025-11-25  08:48AM   
2    NVDA  2025-11-25  08:46AM   
3    NVDA  2025-11-25  08:45AM   
4    NVDA  2025-11-25  08:44AM   
..    ...         ...      ...   
95   NVDA  2025-11-24  12:09PM   
96   NVDA  2025-11-24  12:06PM   
97   NVDA  2025-11-24  12:03PM   
98   NVDA  2025-11-24  12:00PM   
99   NVDA  2025-11-24  12:00PM   

                                             Headline  polarity  
0   Google In Talks To Offer Its AI Chips To Meta;...        -1  
1   Stock Market Today: Dow Jones Rises At Key Lev...         1  
2   Soft Retail Sales, Weak ADP Jobs Data May Shap...        -1  
3   Google Just Hit the AI Accelerator--Is Nvidia'...        -1  
4   Meta Platforms Weighs Multi-Billion-Dollar Dea...         1  
..                                                ...       ...  
95  Alibaba Stock Jumps On Monday -- Here's What Y...         1  
96  Neobank Revolut Boosts Valuation to $75 Billio...         1  
97  Nvidia Stock Rises. The Tech Rally, China News...         1  
98  Elfun Trusts Significantly Reduces Stake in Br...         1  
99  1 Beaten-Down Artificial Intelligence (AI) Sto...        -1  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           NVDA                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  38.00%                                    ║
║  Negative   :  26.00%                                    ║
║  Neutral    :  36.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.1200                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title AAPL
ticker = 'AAPL'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=AAPL


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0    AAPL  2025-11-25  08:46AM   
1    AAPL  2025-11-25  08:25AM   
2    AAPL  2025-11-25  08:20AM   
3    AAPL  2025-11-25  06:40AM   
4    AAPL  2025-11-25  05:36AM   
..    ...         ...      ...   
95   AAPL  2025-11-20  06:00PM   
96   AAPL  2025-11-20  05:43PM   
97   AAPL  2025-11-20  04:38PM   
98   AAPL  2025-11-20  03:36PM   
99   AAPL  2025-11-20  12:26PM   

                                             Headline  
0   Trump's $21 Trillion Boom: Hype or Historic Wi...  
1   Wedbushs Ives lists top 10 tech stocks to own ...  
2   Tesla Stock Could Hit $525, Analyst Says. Lega...  
3   Apple and Alphabet Ordered by Singapore to Cur...  
4   Berkshire Hathaway Stock: Is BRK.B Outperformi...  
..                                                ...  
95  Intrinsic, an Alphabet company, and Nvidia sup...  
96  Google Launches Unauthorized Pixel-to-iPhone F...  
97  Google's winning streak continues as viral Nan...  
98  Wall Street Sees a Buying Opportunity in This ...  
99  Big chipmakers evaluating Intels foundry but C...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0    AAPL  2025-11-25  08:46AM   
1    AAPL  2025-11-25  08:25AM   
2    AAPL  2025-11-25  08:20AM   
3    AAPL  2025-11-25  06:40AM   
4    AAPL  2025-11-25  05:36AM   
..    ...         ...      ...   
95   AAPL  2025-11-20  06:00PM   
96   AAPL  2025-11-20  05:43PM   
97   AAPL  2025-11-20  04:38PM   
98   AAPL  2025-11-20  03:36PM   
99   AAPL  2025-11-20  12:26PM   

                                             Headline  polarity  
0   Trump's $21 Trillion Boom: Hype or Historic Wi...         0  
1   Wedbushs Ives lists top 10 tech stocks to own ...         0  
2   Tesla Stock Could Hit $525, Analyst Says. Lega...         1  
3   Apple and Alphabet Ordered by Singapore to Cur...         0  
4   Berkshire Hathaway Stock: Is BRK.B Outperformi...        -1  
..                                                ...       ...  
95  Intrinsic, an Alphabet company, and Nvidia sup...         0  
96  Google Launches Unauthorized Pixel-to-iPhone F...         0  
97  Google's winning streak continues as viral Nan...         1  
98  Wall Street Sees a Buying Opportunity in This ...         1  
99  Big chipmakers evaluating Intels foundry but C...         1  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           AAPL                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  31.00%                                    ║
║  Negative   :  24.00%                                    ║
║  Neutral    :  45.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.0700                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title TSLA
ticker = 'TSLA'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=TSLA


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0    TSLA  2025-11-25  09:00AM   
1    TSLA  2025-11-25  08:42AM   
2    TSLA  2025-11-25  08:25AM   
3    TSLA  2025-11-25  08:20AM   
4    TSLA  2025-11-25  06:47AM   
..    ...         ...      ...   
95   TSLA  2025-11-21  04:06PM   
96   TSLA  2025-11-21  02:31PM   
97   TSLA  2025-11-21  01:36PM   
98   TSLA  2025-11-21  01:29PM   
99   TSLA  2025-11-21  01:17PM   

                                             Headline  
0   Wall Street Price Prediction: Teslas Share Pri...  
1   What Musk And Tesla Are Saying About FSD With ...  
2   Wedbushs Ives lists top 10 tech stocks to own ...  
3   Tesla Stock Could Hit $525, Analyst Says. Lega...  
4   Panasonic's energy unit to supply auto batteri...  
..                                                ...  
95  Tesla stock drops to end the week as robotaxi ...  
96  Michael Burry Says Nvidia Spent $112.5 Billion...  
97  2025 Hasnt Been Pleasant for Tesla Stock. Will...  
98  Tesla Price Target Reaffirmed at $500 by Piper...  
99  Big Tech ETF attempts to bounce as 'Magnificen...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0    TSLA  2025-11-25  09:00AM   
1    TSLA  2025-11-25  08:42AM   
2    TSLA  2025-11-25  08:25AM   
3    TSLA  2025-11-25  08:20AM   
4    TSLA  2025-11-25  06:47AM   
..    ...         ...      ...   
95   TSLA  2025-11-21  04:06PM   
96   TSLA  2025-11-21  02:31PM   
97   TSLA  2025-11-21  01:36PM   
98   TSLA  2025-11-21  01:29PM   
99   TSLA  2025-11-21  01:17PM   

                                             Headline  polarity  
0   Wall Street Price Prediction: Teslas Share Pri...         0  
1   What Musk And Tesla Are Saying About FSD With ...         0  
2   Wedbushs Ives lists top 10 tech stocks to own ...         0  
3   Tesla Stock Could Hit $525, Analyst Says. Lega...         1  
4   Panasonic's energy unit to supply auto batteri...         0  
..                                                ...       ...  
95  Tesla stock drops to end the week as robotaxi ...        -1  
96  Michael Burry Says Nvidia Spent $112.5 Billion...         1  
97  2025 Hasnt Been Pleasant for Tesla Stock. Will...         1  
98  Tesla Price Target Reaffirmed at $500 by Piper...         1  
99  Big Tech ETF attempts to bounce as 'Magnificen...         1  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           TSLA                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  30.00%                                    ║
║  Negative   :  18.00%                                    ║
║  Neutral    :  52.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.1200                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title AMD
ticker = 'AMD'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=AMD


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0     AMD  2025-11-25  08:56AM   
1     AMD  2025-11-25  08:56AM   
2     AMD  2025-11-25  08:25AM   
3     AMD  2025-11-25  08:00AM   
4     AMD  2025-11-25  07:52AM   
..    ...         ...      ...   
95    AMD  2025-11-20  07:38AM   
96    AMD  2025-11-20  06:51AM   
97    AMD  2025-11-20  06:00AM   
98    AMD  2025-11-20  05:38AM   
99    AMD  2025-11-20  05:29AM   

                                             Headline  
0   Google In Talks To Offer Its AI Chips To Meta;...  
1   Stock Market Today: Dow Jones Rises At Key Lev...  
2   Wedbushs Ives lists top 10 tech stocks to own ...  
3   Stock Market Today: Dow Jones Wavers At Key Le...  
4   Nvidia and AMD stock falls amid Meta-Google AI...  
..                                                ...  
95  CoreWeave, AMD, Super Micro and More. Why Thes...  
96  Advanced Micro Devices receives cautious outlo...  
97  IBM, Cisco Unveil Quantum Networking Plans. Th...  
98  These Stocks Are Moving the Most Today: Nvidia...  
99  Global tech shares surge as Nvidia's AI boom p...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0     AMD  2025-11-25  08:56AM   
1     AMD  2025-11-25  08:56AM   
2     AMD  2025-11-25  08:25AM   
3     AMD  2025-11-25  08:00AM   
4     AMD  2025-11-25  07:52AM   
..    ...         ...      ...   
95    AMD  2025-11-20  07:38AM   
96    AMD  2025-11-20  06:51AM   
97    AMD  2025-11-20  06:00AM   
98    AMD  2025-11-20  05:38AM   
99    AMD  2025-11-20  05:29AM   

                                             Headline  polarity  
0   Google In Talks To Offer Its AI Chips To Meta;...        -1  
1   Stock Market Today: Dow Jones Rises At Key Lev...         1  
2   Wedbushs Ives lists top 10 tech stocks to own ...         0  
3   Stock Market Today: Dow Jones Wavers At Key Le...        -1  
4   Nvidia and AMD stock falls amid Meta-Google AI...        -1  
..                                                ...       ...  
95  CoreWeave, AMD, Super Micro and More. Why Thes...         1  
96  Advanced Micro Devices receives cautious outlo...        -1  
97  IBM, Cisco Unveil Quantum Networking Plans. Th...         0  
98  These Stocks Are Moving the Most Today: Nvidia...         0  
99  Global tech shares surge as Nvidia's AI boom p...         1  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           AMD                            ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  33.00%                                    ║
║  Negative   :  29.00%                                    ║
║  Neutral    :  38.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.0400                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title META
ticker = 'META'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=META


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0    META  2025-11-25  08:56AM   
1    META  2025-11-25  08:56AM   
2    META  2025-11-25  08:46AM   
3    META  2025-11-25  08:45AM   
4    META  2025-11-25  08:44AM   
..    ...         ...      ...   
95   META  2025-11-21  08:01PM   
96   META  2025-11-21  06:51PM   
97   META  2025-11-21  06:31PM   
98   META  2025-11-21  05:32PM   
99   META  2025-11-21  04:51PM   

                                             Headline  
0   Google In Talks To Offer Its AI Chips To Meta;...  
1   Stock Market Today: Dow Jones Rises At Key Lev...  
2   Soft Retail Sales, Weak ADP Jobs Data May Shap...  
3   Google Just Hit the AI Accelerator--Is Nvidia'...  
4   Meta Platforms Weighs Multi-Billion-Dollar Dea...  
..                                                ...  
95  'Crypto Is Now Being Used More Deliberately As...  
96     Mag 7 Earnings Outlook Improves: A Closer Look  
97  A Caller Asks About Student Loan Forgiveness A...  
98  A Magnificent AI Bet? Stanley Druckenmiller's ...  
99  Lillys Sharp Rally Brings Market Cap to $1 Tri...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0    META  2025-11-25  08:56AM   
1    META  2025-11-25  08:56AM   
2    META  2025-11-25  08:46AM   
3    META  2025-11-25  08:45AM   
4    META  2025-11-25  08:44AM   
..    ...         ...      ...   
95   META  2025-11-21  08:01PM   
96   META  2025-11-21  06:51PM   
97   META  2025-11-21  06:31PM   
98   META  2025-11-21  05:32PM   
99   META  2025-11-21  04:51PM   

                                             Headline  polarity  
0   Google In Talks To Offer Its AI Chips To Meta;...        -1  
1   Stock Market Today: Dow Jones Rises At Key Lev...         1  
2   Soft Retail Sales, Weak ADP Jobs Data May Shap...        -1  
3   Google Just Hit the AI Accelerator--Is Nvidia'...        -1  
4   Meta Platforms Weighs Multi-Billion-Dollar Dea...         1  
..                                                ...       ...  
95  'Crypto Is Now Being Used More Deliberately As...         0  
96     Mag 7 Earnings Outlook Improves: A Closer Look         1  
97  A Caller Asks About Student Loan Forgiveness A...         0  
98  A Magnificent AI Bet? Stanley Druckenmiller's ...         0  
99  Lillys Sharp Rally Brings Market Cap to $1 Tri...         1  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           META                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  25.00%                                    ║
║  Negative   :  24.00%                                    ║
║  Neutral    :  51.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.0100                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title MSFT
ticker = 'MSFT'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=MSFT


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0    MSFT  2025-11-25  08:27AM   
1    MSFT  2025-11-25  08:25AM   
2    MSFT  2025-11-25  07:42AM   
3    MSFT  2025-11-25  07:30AM   
4    MSFT  2025-11-25  06:45AM   
..    ...         ...      ...   
95   MSFT  2025-11-21  04:18PM   
96   MSFT  2025-11-21  01:27PM   
97   MSFT  2025-11-21  01:22PM   
98   MSFT  2025-11-21  01:17PM   
99   MSFT  2025-11-21  01:11PM   

                                             Headline  
0   Microsoft, NVIDIA, Anthropic Announce Major AI...  
1   Wedbushs Ives lists top 10 tech stocks to own ...  
2   Anthropic Rolls Out Claude Opus 4.5 With Big P...  
3   Tech Weekly: Nvidia pushes back on 'AI bubble'...  
4   Ming-Chi Kuo Fires Back At Nvidia 'Fraud' Crit...  
..                                                ...  
95  Google Surpasses Microsoft in Market Value. Wh...  
96  Anthropic Just Became AI's Hottest Ticket-Back...  
97  The Bull Case for AI Stocks Is Far Weaker Than...  
98  Big Tech ETF attempts to bounce as 'Magnificen...  
99  UiPath Stock is Consolidating This Year: What ...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0    MSFT  2025-11-25  08:27AM   
1    MSFT  2025-11-25  08:25AM   
2    MSFT  2025-11-25  07:42AM   
3    MSFT  2025-11-25  07:30AM   
4    MSFT  2025-11-25  06:45AM   
..    ...         ...      ...   
95   MSFT  2025-11-21  04:18PM   
96   MSFT  2025-11-21  01:27PM   
97   MSFT  2025-11-21  01:22PM   
98   MSFT  2025-11-21  01:17PM   
99   MSFT  2025-11-21  01:11PM   

                                             Headline  polarity  
0   Microsoft, NVIDIA, Anthropic Announce Major AI...         0  
1   Wedbushs Ives lists top 10 tech stocks to own ...         0  
2   Anthropic Rolls Out Claude Opus 4.5 With Big P...         1  
3   Tech Weekly: Nvidia pushes back on 'AI bubble'...         1  
4   Ming-Chi Kuo Fires Back At Nvidia 'Fraud' Crit...        -1  
..                                                ...       ...  
95  Google Surpasses Microsoft in Market Value. Wh...         1  
96  Anthropic Just Became AI's Hottest Ticket-Back...         0  
97  The Bull Case for AI Stocks Is Far Weaker Than...        -1  
98  Big Tech ETF attempts to bounce as 'Magnificen...         1  
99  UiPath Stock is Consolidating This Year: What ...         0  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           MSFT                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  35.00%                                    ║
║  Negative   :  19.00%                                    ║
║  Neutral    :  46.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.1600                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title GOOGL
ticker = 'GOOGL'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=GOOGL


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0   GOOGL  2025-11-25  09:01AM   
1   GOOGL  2025-11-25  08:56AM   
2   GOOGL  2025-11-25  08:56AM   
3   GOOGL  2025-11-25  08:46AM   
4   GOOGL  2025-11-25  08:45AM   
..    ...         ...      ...   
95  GOOGL  2025-11-24  01:14PM   
96  GOOGL  2025-11-24  01:12PM   
97  GOOGL  2025-11-24  01:11PM   
98  GOOGL  2025-11-24  01:07PM   
99  GOOGL  2025-11-24  01:06PM   

                                             Headline  
0   Bill Nygren's Strategic Moves: Centene Corp Ex...  
1   Google In Talks To Offer Its AI Chips To Meta;...  
2   Stock Market Today: Dow Jones Rises At Key Lev...  
3   Soft Retail Sales, Weak ADP Jobs Data May Shap...  
4   Google Just Hit the AI Accelerator--Is Nvidia'...  
..                                                ...  
95  Amazon to spend $50B on AI, Google & Broadcom ...  
96  Amazon to invest $50 billion in data centers t...  
97  Playing for Legacy: Buffetts Big Bet on Alphab...  
98  Factbox-Tech companies tap debt markets to fun...  
99  Wall Street Weighs New AI Stock Fear: Why Goog...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0   GOOGL  2025-11-25  09:01AM   
1   GOOGL  2025-11-25  08:56AM   
2   GOOGL  2025-11-25  08:56AM   
3   GOOGL  2025-11-25  08:46AM   
4   GOOGL  2025-11-25  08:45AM   
..    ...         ...      ...   
95  GOOGL  2025-11-24  01:14PM   
96  GOOGL  2025-11-24  01:12PM   
97  GOOGL  2025-11-24  01:11PM   
98  GOOGL  2025-11-24  01:07PM   
99  GOOGL  2025-11-24  01:06PM   

                                             Headline  polarity  
0   Bill Nygren's Strategic Moves: Centene Corp Ex...        -1  
1   Google In Talks To Offer Its AI Chips To Meta;...        -1  
2   Stock Market Today: Dow Jones Rises At Key Lev...         1  
3   Soft Retail Sales, Weak ADP Jobs Data May Shap...        -1  
4   Google Just Hit the AI Accelerator--Is Nvidia'...        -1  
..                                                ...       ...  
95  Amazon to spend $50B on AI, Google & Broadcom ...         1  
96  Amazon to invest $50 billion in data centers t...         0  
97  Playing for Legacy: Buffetts Big Bet on Alphab...         1  
98  Factbox-Tech companies tap debt markets to fun...         0  
99  Wall Street Weighs New AI Stock Fear: Why Goog...        -1  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                          GOOGL                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  36.00%                                    ║
║  Negative   :  20.00%                                    ║
║  Neutral    :  44.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.1600                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title AMZN
ticker = 'AMZN'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=AMZN


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0    AMZN  2025-11-25  08:26AM   
1    AMZN  2025-11-25  07:06AM   
2    AMZN  2025-11-25  07:03AM   
3    AMZN  2025-11-25  06:47AM   
4    AMZN  2025-11-25  06:40AM   
..    ...         ...      ...   
95   AMZN  2025-11-22  04:01PM   
96   AMZN  2025-11-22  03:17PM   
97   AMZN  2025-11-22  02:31PM   
98   AMZN  2025-11-22  12:00PM   
99   AMZN  2025-11-22  11:30AM   

                                             Headline  
0   Alphabet Could Hit a $4 Trillion Valuation Tod...  
1                        Where Will UPS Be in 1 Year?  
2   Alphabet Nears a $4 Trillion Valuation as It T...  
3   Panasonic's energy unit to supply auto batteri...  
4   Amazon Pushes Engineers Toward In-House Kiro A...  
..                                                ...  
95  I Just Retired At 62 With $980K Between My 401...  
96  Billionaire Stanley Druckenmiller Just Bought ...  
97  'It's A Never-Ending Merry-Go-Round,' Says Dav...  
98  Quantum Computing Stocks: How the Quantum Comp...  
99  Washington man spent 31 years at Microsoft onl...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0    AMZN  2025-11-25  08:26AM   
1    AMZN  2025-11-25  07:06AM   
2    AMZN  2025-11-25  07:03AM   
3    AMZN  2025-11-25  06:47AM   
4    AMZN  2025-11-25  06:40AM   
..    ...         ...      ...   
95   AMZN  2025-11-22  04:01PM   
96   AMZN  2025-11-22  03:17PM   
97   AMZN  2025-11-22  02:31PM   
98   AMZN  2025-11-22  12:00PM   
99   AMZN  2025-11-22  11:30AM   

                                             Headline  polarity  
0   Alphabet Could Hit a $4 Trillion Valuation Tod...         1  
1                        Where Will UPS Be in 1 Year?         0  
2   Alphabet Nears a $4 Trillion Valuation as It T...        -1  
3   Panasonic's energy unit to supply auto batteri...         0  
4   Amazon Pushes Engineers Toward In-House Kiro A...         1  
..                                                ...       ...  
95  I Just Retired At 62 With $980K Between My 401...         0  
96  Billionaire Stanley Druckenmiller Just Bought ...         0  
97  'It's A Never-Ending Merry-Go-Round,' Says Dav...         0  
98  Quantum Computing Stocks: How the Quantum Comp...         0  
99  Washington man spent 31 years at Microsoft onl...         0  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           AMZN                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  37.00%                                    ║
║  Negative   :  13.00%                                    ║
║  Neutral    :  50.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.2400                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title JPM
ticker = 'JPM'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=JPM


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0     JPM  2025-11-25  06:49AM   
1     JPM  2025-11-25  05:56AM   
2     JPM  2025-11-25  05:44AM   
3     JPM  2025-11-24  04:15PM   
4     JPM  2025-11-24  04:15PM   
..    ...         ...      ...   
95    JPM  2025-11-12  01:12PM   
96    JPM  2025-11-12  01:10PM   
97    JPM  2025-11-12  01:01PM   
98    JPM  2025-11-12  01:00PM   
99    JPM  2025-11-12  12:50PM   

                                             Headline  
0   Wall Streets Macro Traders Eye Their Biggest H...  
1   JPM's Misra Says This Is Not the Time for Pass...  
2   Is JPMorgan Chase Stock Underperforming the Na...  
3   JPMorgan Chase Financial Company LLC Declares ...  
4   JPMorgan and Goldman Upgrade MP Materials Amid...  
..                                                ...  
95  Morgan Stanley, Chubb, and 4 Other Financial S...  
96  Dow's new high ahead of House vote, Trump to h...  
97  Jamie Dimon Unveils JPMorgan's $3 Billion HQ W...  
98  JPMorganChase Expands J.P. Morgan Private Clie...  
99     J.P. Morgan goes Overweight on 3 crypto stocks  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0     JPM  2025-11-25  06:49AM   
1     JPM  2025-11-25  05:56AM   
2     JPM  2025-11-25  05:44AM   
3     JPM  2025-11-24  04:15PM   
4     JPM  2025-11-24  04:15PM   
..    ...         ...      ...   
95    JPM  2025-11-12  01:12PM   
96    JPM  2025-11-12  01:10PM   
97    JPM  2025-11-12  01:01PM   
98    JPM  2025-11-12  01:00PM   
99    JPM  2025-11-12  12:50PM   

                                             Headline  polarity  
0   Wall Streets Macro Traders Eye Their Biggest H...        -1  
1   JPM's Misra Says This Is Not the Time for Pass...         0  
2   Is JPMorgan Chase Stock Underperforming the Na...        -1  
3   JPMorgan Chase Financial Company LLC Declares ...         0  
4   JPMorgan and Goldman Upgrade MP Materials Amid...         1  
..                                                ...       ...  
95  Morgan Stanley, Chubb, and 4 Other Financial S...         0  
96  Dow's new high ahead of House vote, Trump to h...         1  
97  Jamie Dimon Unveils JPMorgan's $3 Billion HQ W...         0  
98  JPMorganChase Expands J.P. Morgan Private Clie...         0  
99     J.P. Morgan goes Overweight on 3 crypto stocks         0  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           JPM                            ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  27.00%                                    ║
║  Negative   :  21.00%                                    ║
║  Neutral    :  52.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : +0.0600                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title COIN
ticker = 'COIN'

# Web scrape the news

finviz_url = "https://finviz.com/quote.ashx?t="


news_tables = {}
url = finviz_url + ticker
print(url)
t_content = requests.get(url, headers = agent_info)
content_bs = bs(t_content.content, "html")
news_tab = content_bs.find(id="news-table")
news_tables[ticker] =news_tab

https://finviz.com/quote.ashx?t=COIN


In [ ]:
table_array = []

for name, news_table in news_tables.items():
    for x in news_table.find_all('tr'):
        try:
          #headline
          text_content = x.a.get_text()
          #dates
          date_content = x.td.text.split()

          if len(date_content) == 1:
              time = date_content[0]
          else:
              date= date_content[0]
              time = date_content[1]

          table_array.append([name,date, time, text_content])

        except:
          continue

table_news = pd.DataFrame(table_array, columns=["Ticker","Date","Time","Headline"])

table_news['Date'] = np.where(table_news['Date']=="Today", datetime.date.today(), table_news['Date'])
table_news['Date'] = pd.to_datetime(table_news['Date']).dt.date

table_news

Ticker        Date     Time  \
0    COIN  2025-11-25  08:53AM   
1    COIN  2025-11-25  08:07AM   
2    COIN  2025-11-25  05:26AM   
3    COIN  2025-11-25  04:47AM   
4    COIN  2025-11-24  10:56PM   
..    ...         ...      ...   
95   COIN  2025-11-17  09:01AM   
96   COIN  2025-11-17  09:00AM   
97   COIN  2025-11-17  06:55AM   
98   COIN  2025-11-17  06:25AM   
99   COIN  2025-11-17  03:48AM   

                                             Headline  
0   Strategy, Robinhood and Coinbase Stocks Slide....  
1   Goldman Sachs Lowers Coinbase (COIN) PT to $31...  
2   Coinbase Announces Next Chapter In December: H...  
3   Will Coinbase Pump Monad Crypto? Monad Crypto ...  
4            Bitcoin Rebounds Above $88KWill It Last?  
..                                                ...  
95             Morning Minute: The DAT Meltdown Is On  
96  Is Trending Stock Coinbase Global, Inc. (COIN)...  
97  Coinbase vs. Robinhood Stock: One Will Upgrade...  
98  Coinbase's $375 Million Echo Deal Is Part of a...  
99  Investigative Reporter Group ICIJ Exposes Coin...  

[100 rows x 4 columns]

In [ ]:
table_news['polarity'] = table_news['Headline'].apply(lambda x: getLmScore(lm_sentiment(x)))
table_news

Ticker        Date     Time  \
0    COIN  2025-11-25  08:53AM   
1    COIN  2025-11-25  08:07AM   
2    COIN  2025-11-25  05:26AM   
3    COIN  2025-11-25  04:47AM   
4    COIN  2025-11-24  10:56PM   
..    ...         ...      ...   
95   COIN  2025-11-17  09:01AM   
96   COIN  2025-11-17  09:00AM   
97   COIN  2025-11-17  06:55AM   
98   COIN  2025-11-17  06:25AM   
99   COIN  2025-11-17  03:48AM   

                                             Headline  polarity  
0   Strategy, Robinhood and Coinbase Stocks Slide....         0  
1   Goldman Sachs Lowers Coinbase (COIN) PT to $31...        -1  
2   Coinbase Announces Next Chapter In December: H...         0  
3   Will Coinbase Pump Monad Crypto? Monad Crypto ...         0  
4            Bitcoin Rebounds Above $88KWill It Last?         1  
..                                                ...       ...  
95             Morning Minute: The DAT Meltdown Is On         0  
96  Is Trending Stock Coinbase Global, Inc. (COIN)...         1  
97  Coinbase vs. Robinhood Stock: One Will Upgrade...         1  
98  Coinbase's $375 Million Echo Deal Is Part of a...         0  
99  Investigative Reporter Group ICIJ Exposes Coin...         0  

[100 rows x 5 columns]

In [ ]:
import plotly.express as px

df_pie = table_news.groupby('polarity').count().reset_index()
df_pie.rename(columns={'Headline' : 'count'}, inplace=True)

fig = px.pie(df_pie, values='count', names='polarity', title='Sentiment Distribution')
fig.show()

In [ ]:
# Calculate percentages
sentiment_counts = table_news['polarity'].value_counts(normalize=True).sort_index()
pos_pct = sentiment_counts.get(1, 0) * 100
neg_pct = sentiment_counts.get(-1, 0) * 100
neu_pct = sentiment_counts.get(0, 0) * 100

# Net sentiment score (-1 to +1)
net_score = (pos_pct/100 * 1) + (neg_pct/100 * -1)

# === Your exact trading logic ===
if pos_pct > 40:
    signal = "BUY (Long)"
    direction = "Bullish"
    emoji = "Green Up Arrow"
    color = "\033[92m"  # Green
elif neg_pct > 40:
    signal = "SELL SHORT"
    direction = "Bearish"
    emoji = "Red Down Arrow"
    color = "\033[91m"  # Red
else:
    signal = "NO ACTION"
    direction = "Neutral / Wait"
    emoji = "Yellow Circle"
    color = "\033[93m"  # Yellow

# === Beautiful output ===
reset = "\033[0m"
print(f"""
╔{'═' * 58}╗
║{' FINVIZ NEWS SENTIMENT ANALYSIS ':^58}║
║{' ' + ticker.upper().center(56) + ' '}║
╠{'═' * 58}╣
║  Positive   : {pos_pct:6.2f}%                                    ║
║  Negative   : {neg_pct:6.2f}%                                    ║
║  Neutral    : {neu_pct:6.2f}%                                    ║
╠{'═' * 58}╣
║  Net Sentiment Score : {net_score:+.4f} {' ':>26}║
╠{'═' * 58}╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       {color}▶▶ {signal.upper():^35} ◀◀{reset}        ║
║       {emoji}  Market Tone: {direction:^20}   ║
║                                                          ║
╚{'═' * 58}╝
""")

# Optional: one-liner for backtesting / logging
print(f"→ {ticker} | Pos:{pos_pct:.1f}% Neg:{neg_pct:.1f}% | Score:{net_score:+.3f} | Signal: {signal}")


╔══════════════════════════════════════════════════════════╗
║              FINVIZ NEWS SENTIMENT ANALYSIS              ║
║                           COIN                           ║
╠══════════════════════════════════════════════════════════╣
║  Positive   :  19.00%                                    ║
║  Negative   :  22.00%                                    ║
║  Neutral    :  59.00%                                    ║
╠══════════════════════════════════════════════════════════╣
║  Net Sentiment Score : -0.0300                           ║
╠══════════════════════════════════════════════════════════╣
║                                                          ║
║   RECOMMENDED ACTION:                                    ║
║                                                          ║
║       ▶▶              NO ACTION              ◀◀        ║
║       Yellow Circle  Market Tone:    Neutral / Wait      ║
║                                                          ║
╚════════════════════════

In [ ]:
#@title Auto batch

import pandas as pd
from datetime import datetime

# === FIXED getLmScore that works with both single & batch inference ===
def getLmScore(item):
    # item is either: [{'label': ..., 'score': ...}] or directly {'label': ..., 'score': ...}
    if isinstance(item, list):
        x = item[0]
    else:
        x = item
    label = x['label'].lower()
    if label == "positive":
        return 1
    elif label == "negative":
        return -1
    else:
        return 0

# Your 10 tickers
tickers = ['NVDA', 'AAPL', 'TSLA', 'AMD', 'META', 'MSFT', 'GOOGL', 'AMZN', 'JPM', 'COIN']

results = []
print("Running sentiment analysis on 10 stocks...\n")

for i, ticker in enumerate(tickers, 1):
    print(f"({i:2}/10) {ticker:<6}", end=" → ")

    url = f"https://finviz.com/quote.ashx?t={ticker}"
    headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36'}

    try:
        r = requests.get(url, headers=headers, timeout=10)
        soup = bs(r.content, "html.parser")
        news_table = soup.find(id="news-table")

        headlines = []
        for row in news_table.find_all('tr'):
            text = row.find('a')
            if text:
                headlines.append(text.get_text())

        if not headlines:
            print("No headlines found")
            continue

        # Batch inference (very fast)
        predictions = lm_sentiment(headlines, batch_size=32, truncation=True, max_length=512)

        # Now works perfectly
        polarity_scores = [getLmScore(pred) for pred in predictions]

        pos_pct = sum(1 for s in polarity_scores if s == 1) / len(polarity_scores) * 100
        neg_pct = sum(1 for s in polarity_scores if s == -1) / len(polarity_scores) * 100
        neu_pct = 100 - pos_pct - neg_pct
        net_score = (pos_pct - neg_pct) / 100

        signal = "BUY (Long)" if pos_pct > 40 else "SELL SHORT" if neg_pct > 40 else "NO ACTION"

        results.append({
            'Date': datetime.now().strftime('%Y-%m-%d'),
            'Ticker': ticker,
            'Headlines': len(headlines),
            'Positive_%': round(pos_pct, 2),
            'Negative_%': round(neg_pct, 2),
            'Neutral_%': round(neu_pct, 2),
            'Net_Score': round(net_score, 4),
            'Signal': signal
        })

        print(f"Positive {pos_pct:5.1f}% | Negative {neg_pct:5.1f}% → {signal}")

    except Exception as e:
        print(f"Error: {e}")

# === Final DataFrame & Save CSV ===
df_results = pd.DataFrame(results)

csv_name = f"FinViz_Sentiment_10Stocks_{datetime.now().strftime('%Y%m%d_%H%M')}.csv"
df_results.to_csv(csv_name, index=False)

# === Beautiful Display ===
from IPython.display import display
print("\n" + "═" * 80)
print(" " * 25 + "FINAL SENTIMENT SUMMARY (10 STOCKS)")
print("═" * 80)
display(df_results.style
        .bar(subset=['Net_Score'], align='mid', color=['#d65f5f', '#5fba7d'])
        .format({'Positive_%': '{:.1f}%', 'Negative_%': '{:.1f}%', 'Neutral_%': '{:.1f}%'}))

print(f"\nCSV saved → {csv_name}")
print(f"Total headlines analyzed: {df_results['Headlines'].sum():,}")

Running sentiment analysis on 10 stocks...

( 1/10) NVDA   → Positive  38.0% | Negative  26.0% → NO ACTION
( 2/10) AAPL   → Positive  31.0% | Negative  24.0% → NO ACTION
( 3/10) TSLA   → Positive  30.0% | Negative  18.0% → NO ACTION
( 4/10) AMD    → Positive  33.0% | Negative  29.0% → NO ACTION
( 5/10) META   → Positive  25.0% | Negative  24.0% → NO ACTION
( 6/10) MSFT   → Positive  35.0% | Negative  19.0% → NO ACTION
( 7/10) GOOGL  → Positive  36.0% | Negative  20.0% → NO ACTION
( 8/10) AMZN   → Positive  37.0% | Negative  13.0% → NO ACTION
( 9/10) JPM    → Positive  27.0% | Negative  21.0% → NO ACTION
(10/10) COIN   → Positive  19.0% | Negative  22.0% → NO ACTION

════════════════════════════════════════════════════════════════════════════════
                         FINAL SENTIMENT SUMMARY (10 STOCKS)
════════════════════════════════════════════════════════════════════════════════



CSV saved → FinViz_Sentiment_10Stocks_20251125_1413.csv
Total headlines analyzed: 1,000
